In [1]:
from textwrap import dedent
from agno.agent import Agent
from agno.models.openai import OpenAILike
from agno.memory.v2.db.sqlite import SqliteMemoryDb
from agno.exceptions import StopAgentRun
from agno.memory.v2.memory import Memory
from agno.tools import tool,FunctionCall
from agno.tools.dalle import DalleTools
from agno.storage.sqlite import SqliteStorage

from dotenv import load_dotenv 

from typing import List,Iterator
from pydantic import BaseModel, Field

from rich.console import Console
from rich.prompt import Prompt
from rich.pretty import pprint

import httpx
import os
import json
load_dotenv()


True

**agent state**

In [2]:
# Define a tool that adds an item to the shopping list
def add_item(agent: Agent, item: str) -> str:
    """Add an item to the shopping list."""
    if agent.session_state is None:
        agent.session_state = {}
    if "shopping_list" not in agent.session_state:
        agent.session_state["shopping_list"] = []
    agent.session_state["shopping_list"].append(item)
    return f"The shopping list is now {agent.session_state['shopping_list']}"

agent = Agent(
name="my_agent",
model=OpenAILike(id="qwen3-30b-a3b", 
    api_key=os.getenv("BAILIAN_API_KEY"), 
    base_url=os.getenv("BAILIAN_API_BASE_URL"),
    request_params={"extra_body": {"enable_thinking": False}},),
markdown=True,
# Initialize the session state with a counter starting at 0
session_state={"shopping_list": []},
tools=[add_item],
# You can use variables from the session state in the instructions
instructions="Current state (shopping list) is: {shopping_list}",
# Important: Add the state to the messages
add_state_in_messages=True,
)

# Example usage
agent.print_response("Add milk, eggs, and bread to the shopping list", stream=True)
print(f"Final session state: {agent.session_state}")

Output()

Final session state: {'shopping_list': ['milk', 'eggs', 'bread'], 'current_session_id': 'c0e056e2-5ea1-4e62-a955-227f6485ffa6'}


In [ ]:
# Define tools to manage our shopping list
@tool(description="Add an item to the shopping list.")
def add_item(agent: Agent, item: str) -> str:
    """Add an item to the shopping list and return confirmation."""
    # Add the item if it's not already in the list
    if agent.session_state is None:
        agent.session_state = {}
    if "shopping_list" not in agent.session_state:
        agent.session_state["shopping_list"] = []

    # Add the item if it's not already in the list
    if item.lower() not in [i.lower() for i in agent.session_state["shopping_list"]]:
        agent.session_state["shopping_list"].append(item)
        return f"Added '{item}' to the shopping list"
    else:
        return f"'{item}' is already in the shopping list"

@tool(description="Remove an item from the shopping list by name.")
def remove_item(agent: Agent, item: str) -> str:
    """Remove an item from the shopping list by name."""
    # Case-insensitive search
    if agent.session_state is None:
        agent.session_state = {}
    if "shopping_list" not in agent.session_state:
        agent.session_state["shopping_list"] = []

    for i, list_item in enumerate(agent.session_state["shopping_list"]):
        if list_item.lower() == item.lower():
            agent.session_state["shopping_list"].pop(i)
            return f"Removed '{list_item}' from the shopping list"

    return f"'{item}' was not found in the shopping list"

@tool(description="List all items in the shopping list.")
def list_items(agent: Agent) -> str:
    """List all items in the shopping list."""
    if agent.session_state is None:
        agent.session_state = {}
    if "shopping_list" not in agent.session_state:
        agent.session_state["shopping_list"] = []
        
    shopping_list = agent.session_state["shopping_list"]

    if not shopping_list:
        return "The shopping list is empty."

    items_text = "\n".join([f"- {item}" for item in shopping_list])
    return f"Current shopping list:\n{items_text}"


# Create a Shopping List Manager Agent that maintains state
agent = Agent(
    model=OpenAILike(id="qwen3-30b-a3b", 
    api_key=os.getenv("BAILIAN_API_KEY"), 
    base_url=os.getenv("BAILIAN_API_BASE_URL"),
    request_params={"extra_body": {"enable_thinking": False}},),
    # Initialize the session state with an empty shopping list
    session_state={"shopping_list": []},
    tools=[add_item, remove_item, list_items],
    # You can use variables from the session state in the instructions
    instructions=dedent("""\
        Your job is to manage a shopping list.

        The shopping list starts empty. You can add items, remove items by name, and list all items.

        Current shopping list: {shopping_list}
    """),
    show_tool_calls=True,
    add_state_in_messages=True,
    markdown=True,
)

# Example usage
agent.print_response("Add milk, eggs, and bread to the shopping list", stream=True)
print(f"Session state: {agent.session_state}")

agent.print_response("I got bread", stream=True)
print(f"Session state: {agent.session_state}")

agent.print_response("I need apples and oranges", stream=True)
print(f"Session state: {agent.session_state}")

agent.print_response("whats on my list?", stream=True)
print(f"Session state: {agent.session_state}")

agent.print_response("Clear everything from my list and start over with just bananas and yogurt", stream=True)
print(f"Session state: {agent.session_state}")

**Memory**

In [ ]:
# UserId for the memories
user_id = "ava"
# Database file for memory and storage
db_file = "temp/agent.db"

# Initialize memory.v2
memory = Memory(
    # Use any model for creating memories
    model=OpenAILike(id="qwen3-30b-a3b", 
                    api_key=os.getenv("BAILIAN_API_KEY"), 
                    base_url=os.getenv("BAILIAN_API_BASE_URL"),
                    request_params={"extra_body": {"enable_thinking": False}},),
    db=SqliteMemoryDb(table_name="user_memories", db_file=db_file),
)
# Initialize storage
storage = SqliteStorage(table_name="agent_sessions", db_file=db_file)

# Initialize Agent
memory_agent = Agent(
    model=OpenAILike(id="qwen3-30b-a3b", 
    api_key=os.getenv("BAILIAN_API_KEY"), 
    base_url=os.getenv("BAILIAN_API_BASE_URL"),
    request_params={"extra_body": {"enable_thinking": False}},),
    # Store memories in a database
    memory=memory,
    # Give the Agent the ability to update memories
    enable_agentic_memory=True,
    # OR - Run the MemoryManager after each response
    enable_user_memories=True,
    # Store the chat history in the database
    storage=storage,
    # Add the chat history to the messages
    add_history_to_messages=True,
    # Number of history runs
    num_history_runs=3,
    markdown=True,
)

memory.clear()
memory_agent.print_response(
    "My name is Ava and I like to ski.",
    user_id=user_id,
    stream=True,
    stream_intermediate_steps=True,
)
print("Memories about Ava:")
pprint(memory.get_user_memories(user_id=user_id))

memory_agent.print_response(
    "I live in san francisco, where should i move within a 4 hour drive?",
    user_id=user_id,
    stream=True,
    stream_intermediate_steps=True,
)
print("Memories about Ava:")
pprint(memory.get_user_memories(user_id=user_id))

**structured output**

In [ ]:
class MovieScript(BaseModel):
    setting: str = Field(
        ...,
        description="A richly detailed, atmospheric description of the movie's primary location and time period. Include sensory details and mood.",
    )
    ending: str = Field(
        ...,
        description="The movie's powerful conclusion that ties together all plot threads. Should deliver emotional impact and satisfaction.",
    )
    genre: str = Field(
        ...,
        description="The film's primary and secondary genres (e.g., 'Sci-fi Thriller', 'Romantic Comedy'). Should align with setting and tone.",
    )
    name: str = Field(
        ...,
        description="An attention-grabbing, memorable title that captures the essence of the story and appeals to target audience.",
    )
    characters: List[str] = Field(
        ...,
        description="4-6 main characters with distinctive names and brief role descriptions (e.g., 'Sarah Chen - brilliant quantum physicist with a dark secret').",
    )
    storyline: str = Field(
        ...,
        description="A compelling three-sentence plot summary: Setup, Conflict, and Stakes. Hook readers with intrigue and emotion.",
    )


# Agent that uses JSON mode
json_mode_agent = Agent(
    model=OpenAILike(id="qwen3-30b-a3b", 
                    api_key=os.getenv("BAILIAN_API_KEY"), 
                    base_url=os.getenv("BAILIAN_API_BASE_URL"),
                    request_params={"extra_body": {"enable_thinking": False}},),
    description=dedent("""\
        You are an acclaimed Hollywood screenwriter known for creating unforgettable blockbusters! 🎬
        With the combined storytelling prowess of Christopher Nolan, Aaron Sorkin, and Quentin Tarantino,
        you craft unique stories that captivate audiences worldwide.

        Your specialty is turning locations into living, breathing characters that drive the narrative.\
    """),
    instructions=dedent("""\
        When crafting movie concepts, follow these principles:

        1. Settings should be characters:
           - Make locations come alive with sensory details
           - Include atmospheric elements that affect the story
           - Consider the time period's impact on the narrative

        2. Character Development:
           - Give each character a unique voice and clear motivation
           - Create compelling relationships and conflicts
           - Ensure diverse representation and authentic backgrounds

        3. Story Structure:
           - Begin with a hook that grabs attention
           - Build tension through escalating conflicts
           - Deliver surprising yet inevitable endings

        4. Genre Mastery:
           - Embrace genre conventions while adding fresh twists
           - Mix genres thoughtfully for unique combinations
           - Maintain consistent tone throughout

        Transform every location into an unforgettable cinematic experience!\
    """),
    response_model=MovieScript,
    use_json_mode=True,
)

# Agent that uses structured outputs
structured_output_agent = Agent(
    model=OpenAILike(id="qwen3-30b-a3b", 
                    api_key=os.getenv("BAILIAN_API_KEY"), 
                    base_url=os.getenv("BAILIAN_API_BASE_URL"),
                    request_params={"extra_body": {"enable_thinking": False}},),
    description=dedent("""\
        You are an acclaimed Hollywood screenwriter known for creating unforgettable blockbusters! 🎬
        With the combined storytelling prowess of Christopher Nolan, Aaron Sorkin, and Quentin Tarantino,
        you craft unique stories that captivate audiences worldwide.

        Your specialty is turning locations into living, breathing characters that drive the narrative.\
    """),
    instructions=dedent("""\
        When crafting movie concepts in json, follow these principles:

        1. Settings should be characters:
           - Make locations come alive with sensory details
           - Include atmospheric elements that affect the story
           - Consider the time period's impact on the narrative

        2. Character Development:
           - Give each character a unique voice and clear motivation
           - Create compelling relationships and conflicts
           - Ensure diverse representation and authentic backgrounds

        3. Story Structure:
           - Begin with a hook that grabs attention
           - Build tension through escalating conflicts
           - Deliver surprising yet inevitable endings

        4. Genre Mastery:
           - Embrace genre conventions while adding fresh twists
           - Mix genres thoughtfully for unique combinations
           - Maintain consistent tone throughout

        Transform every location into an unforgettable cinematic experience!\
    """),
    response_model=MovieScript,
)

structured_output_agent.print_response(
    "New York", stream=True, stream_intermediate_steps=True
)
# Example usage with different locations
json_mode_agent.print_response("Tokyo", stream=True)
structured_output_agent.print_response("Ancient Rome", stream=True)

# More examples to try:
"""
Creative location prompts to explore:
1. "Underwater Research Station" - For a claustrophobic sci-fi thriller
2. "Victorian London" - For a gothic mystery
3. "Dubai 2050" - For a futuristic heist movie
4. "Antarctic Research Base" - For a survival horror story
5. "Caribbean Island" - For a tropical adventure romance
"""

# To get the response in a variable:
# from rich.pretty import pprint

# json_mode_response: RunResponse = json_mode_agent.run("New York")
# pprint(json_mode_response.content)
# structured_output_response: RunResponse = structured_output_agent.run("New York")
# pprint(structured_output_response.content)

**Multimodal Agent**